<a href="https://colab.research.google.com/github/saharnazyp/Sales_forcasting/blob/main/predict_sales.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip -q install lightgbm jdatetime holidays

In [ ]:
pip install pandas numpy scikit-learn lightgbm jdatetime holidays

In [ ]:
import pandas as pd
import numpy as np
from datetime import timedelta
import jdatetime
import holidays
from lightgbm import LGBMRegressor


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:

INPUT_XLSX = "/content/drive/MyDrive/data/sale.xlsx"
DATE_COL = "Date"
BRANCH_COL = "نام شعبه"
ITEM_COL = "کد کالا"
QTY_COL = "تعداد"
HORIZON_DAYS = 30  # پیش‌بینی ۱ ماه

TARGET_Y, TARGET_M = 1404, 12

In [ ]:
def parse_date_auto(x):
    """اگر datetime بود همان را برمی‌گرداند؛ اگر شمسی بود تبدیل می‌کند."""
    if pd.isna(x):
        return np.nan

    # اگر از قبل datetime / Timestamp باشد
    if isinstance(x, (pd.Timestamp,)):
        return x.to_pydatetime()
    if hasattr(x, "year") and hasattr(x, "month") and hasattr(x, "day") and not isinstance(x, str):
        # python datetime/date
        try:
            return pd.to_datetime(x).to_pydatetime()
        except:
            pass

    s = str(x).strip()
    # یکدست‌سازی
    s = s.replace("/", "-").replace(".", "-")

    # اگر فرم شمسی بود 1403-05-21
    parts = s.split("-")
    if len(parts) >= 3:
        y, m, d = int(parts[0]), int(parts[1]), int(parts[2])
        # حدس: اگر سال >= 1300 یعنی شمسی
        if y >= 1300:
            return jdatetime.date(y, m, d).togregorian()
        else:
            # میلادی
            return pd.to_datetime(f"{y:04d}-{m:02d}-{d:02d}").to_pydatetime()

In [ ]:
def parse_jalali_to_gregorian(x):
    if pd.isna(x):
        return np.nan
    s = str(x).strip()

    # Attempt to parse as Gregorian datetime first, to handle 'YYYY-MM-DD HH:MM:SS'
    try:
        dt_obj = pd.to_datetime(s)
        return dt_obj.date() # Return as datetime.date
    except (ValueError, TypeError):
        pass # Not a standard Gregorian datetime string, proceed to Jalali parsing

    # If not parsed as Gregorian, try Jalali format
    s = s.replace("/", "-") # Normalize separators for Jalali

    try:
        y, m, d = map(int, s.split("-"))
        # Heuristic for Jalali years. If year is too small to be a typical Jalali year (e.g., < 1300),
        # it's likely a Gregorian year that somehow passed the first try, or an invalid date.
        if 1300 <= y <= 1500: # A reasonable range for Jalali years
            return jdatetime.date(y, m, d).togregorian()
        else: # If it wasn't parsed as Gregorian datetime, and year is not Jalali-like
              # it's an unidentifiable date or malformed.
            return np.nan # Or raise an error, depending on desired strictness
    except ValueError:
        return np.nan # Unparseable string

ir_holidays = holidays.country_holidays("IR")

def make_features(df):
    df = df.sort_values("date")
    df["dow"] = df["date"].dt.weekday  # 0=Mon
    df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)

    # Lag features
    for lag in [1, 7, 14]:
        df[f"lag_{lag}"] = df[QTY_COL].shift(lag)

    # Rolling means
    df["rmean_7"] = df[QTY_COL].shift(1).rolling(7).mean()
    df["rmean_14"] = df[QTY_COL].shift(1).rolling(14).mean()

    return df

In [ ]:
def parse_jalali_to_gregorian(x):
    if pd.isna(x):
        return np.nan
    s = str(x).strip()

    # Attempt to parse as Gregorian datetime first, to handle 'YYYY-MM-DD HH:MM:SS'
    try:
        dt_obj = pd.to_datetime(s)
        return dt_obj.date() # Return as datetime.date
    except (ValueError, TypeError):
        pass # Not a standard Gregorian datetime string, proceed to Jalali parsing

    # If not parsed as Gregorian, try Jalali format
    s = s.replace("/", "-") # Normalize separators for Jalali

    try:
        y, m, d = map(int, s.split("-"))
        # Heuristic for Jalali years. If year is too small to be a typical Jalali year (e.g., < 1300),
        # it's likely a Gregorian year that somehow passed the first try, or an invalid date.
        if 1300 <= y <= 1500: # A reasonable range for Jalali years
            return jdatetime.date(y, m, d).togregorian()
        else: # If it wasn't parsed as Gregorian datetime, and year is not Jalali-like
              # it's an unidentifiable date or malformed.
            return np.nan # Or raise an error, depending on desired strictness
    except ValueError:
        return np.nan # Unparseable string

ir_holidays = holidays.country_holidays("IR")

def make_features(df):
    df = df.sort_values("date")
    df["dow"] = df["date"].dt.weekday  # 0=Mon
    df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)

    # Lag features
    for lag in [1, 7, 14]:
        df[f"lag_{lag}"] = df[QTY_COL].shift(lag)

    # Rolling means
    df["rmean_7"] = df[QTY_COL].shift(1).rolling(7).mean()
    df["rmean_14"] = df[QTY_COL].shift(1).rolling(14).mean()

    return df

In [ ]:
ITEM_NAME_COL = "نام کالا"

# نگاشت کد کالا -> نام کالا (اگر برای یک کد چند نام دارید، پرتکرارترین را می‌گیرد)
item_map = (
    df[[ITEM_COL, ITEM_NAME_COL]]
    .dropna()
    .groupby(ITEM_COL)[ITEM_NAME_COL]
    .agg(lambda s: s.value_counts().index[0])
    .reset_index()
)


In [ ]:
out_df = out_df.merge(item_map, on=ITEM_COL, how="left")


In [ ]:
out_df = out_df[["date", BRANCH_COL, ITEM_COL, ITEM_NAME_COL, "پیش‌بینی تعداد", "تعطیل رسمی"]]


In [ ]:
df = df.groupby(["date", BRANCH_COL, ITEM_COL], as_index=False)[QTY_COL].sum()


In [ ]:
df = pd.read_excel(INPUT_XLSX)
df["date"] = df[DATE_COL].apply(parse_jalali_to_gregorian)
df["date"] = pd.to_datetime(df["date"])
df = df.sort_values("date")

In [ ]:
# ============ 2) آموزش و پیش‌بینی ============
results = []

for (branch, item), g in df.groupby([BRANCH_COL, ITEM_COL]):
    g = g.copy()
    g = make_features(g)
    g = g.dropna()  # به خاطر lag ها

    if len(g) < 30:
        continue

    FEATURES = ["dow", "is_holiday", "lag_1", "lag_7", "lag_14", "rmean_7", "rmean_14"]
    X = g[FEATURES]
    y = g[QTY_COL]

    model = LGBMRegressor(
        n_estimators=400,
        learning_rate=0.05,
        num_leaves=31,
        random_state=42
    )
    model.fit(X, y)

    # ============ 3) پیش‌بینی ۳۰ روز آینده ============
    last_date = g["date"].max()
    history = g[["date", QTY_COL]].copy()

    future_rows = []
    for i in range(1, HORIZON_DAYS + 1):
        d = last_date + timedelta(days=i)

        row = {
            "date": d,
            "dow": d.weekday(),
            "is_holiday": int(d in ir_holidays)
        }

        def get_lag(k):
            t = d - timedelta(days=k)
            v = history.loc[history["date"] == t, QTY_COL]
            return float(v.values[0]) if len(v) else np.nan

        row["lag_1"] = get_lag(1)
        row["lag_7"] = get_lag(7)
        row["lag_14"] = get_lag(14)

        last_vals = history.sort_values("date").tail(14)[QTY_COL]
        row["rmean_7"] = last_vals.tail(7).mean()
        row["rmean_14"] = last_vals.mean()

        Xf = pd.DataFrame([row])[FEATURES]
        y_pred = max(0, float(model.predict(Xf)[0]))

        history = pd.concat(
            [history, pd.DataFrame([{"date": d, QTY_COL: y_pred}])],
            ignore_index=True
        )

        future_rows.append({
            "date": d,
            BRANCH_COL: branch,
            ITEM_COL: item,
            "پیش‌بینی تعداد": round(y_pred, 2),
            "تعطیل رسمی": row["is_holiday"]
        })

    results.extend(future_rows)


/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)
/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)
/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000099 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 49
[LightGBM] [Info] Number of data points in the train set: 476, number of used features: 7
[LightGBM] [Info] Start training from score 1.300420
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf

/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)
/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000025 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 19
[LightGBM] [Info] Number of data points in the train set: 73, number of used features: 3
[LightGBM] [Info] Start training from score 1.068493
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)
/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)


...

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000070 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 49
[LightGBM] [Info] Number of data points in the train set: 222, number of used features: 7
[LightGBM] [Info] Start training from score 1.265766
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf

/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)
/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000030 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 22
[LightGBM] [Info] Number of data points in the train set: 65, number of used features: 3
[LightGBM] [Info] Start training from score 1.353846
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)
/tmp/ipython-input-2911248032.py:33: FutureWarning: The behavior of 'isin' with dtype=datetime64[ns] and castable values (e.g. strings) is deprecated. In a future version, these will not be considered matching by isin. Explicitly cast to the appropriate dtype before calling isin instead.
  df["is_holiday"] = df["date"].isin(ir_holidays).astype(int)


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000065 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 45
[LightGBM] [Info] Number of data points in the train set: 146, number of used features: 7
[LightGBM] [Info] Start training from score 1.321918
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf

In [ ]:
import os

out_df = pd.DataFrame(results)
out_path = "/mnt/data/forecast_30days_by_branch_item.xlsx"

# Create the directory if it doesn't exist
os.makedirs(os.path.dirname(out_path), exist_ok=True)

out_df.to_excel(out_path, index=False)

print("✅ خروجی ساخته شد:", out_path)

✅ خروجی ساخته شد: /mnt/data/forecast_30days_by_branch_item.xlsx


In [ ]:
from google.colab import files
files.download("/mnt/data/forecast_30days_by_branch_item.xlsx")


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>